In [6]:
import tensorflow as tf
import tensorflow.keras as keras
from tensorflow.keras import metrics
from read_tfrecord import *
from mtcnn_model import Pnet,cls_ohem,bbox_ohem, landmark_ohem
from tqdm import tqdm
import os
import numpy as np

In [7]:
data_path = "data/12/train_PNet_landmark.tfrecord"

In [8]:
def load_pokemon(mode='train'):
    """ 加载pokemon数据集的工具！
    :param root:    数据集存储的目录
    :param mode:    mode:当前加载的数据是train,val,还是test
    :return:
    """
    # # 创建数字编码表,范围0-4;
    # name2label = {}  # "sq...":0   类别名:类标签;  字典 可以看一下目录,一共有5个文件夹,5个类别：0-4范围;
    # for name in sorted(os.listdir(os.path.join(root))):     # 列出所有目录;
    #     if not os.path.isdir(os.path.join(root, name)):
    #         continue
    #     # 给每个类别编码一个数字
    #     name2label[name] = len(name2label.keys())
 
    # 读取Label信息;保存索引文件images.csv
    # [file1,file2,], 对应的标签[3,1] 2个一一对应的list对象。
    # 根据目录,把每个照片的路径提取出来,以及每个照片路径所对应的类别都存储起来，存储到CSV文件中。
    size = 12
    images,labels,boxes,landmarks = red_tf(data_path,size)
 
    # 图片切割成，训练70%，验证15%，测试15%。
    if mode == 'train':                                                     # 70% 训练集
        images = images[:int(0.7 * len(images))]
        labels = labels[:int(0.7 * len(labels))]
        boxes  = boxes[:int(0.7 * len(boxes))]
        landmarks = landmarks[:int(0.7 * len(landmarks))]
    elif mode == 'val':                                                     # 15% = 70%->85%  验证集
        images = images[int(0.7 * len(images)):int(0.85 * len(images))]
        labels = labels[int(0.7 * len(labels)):int(0.85 * len(labels))]
        boxes = boxes[int(0.7 * len(boxes)):int(0.85 * len(boxes))]
        landmarks = landmarks[int(0.7 * len(landmarks)):int(0.85 * len(landmarks))]
    else:                                                                   # 15% = 70%->85%  测试集
        images = images[int(0.85 * len(images)):]
        labels = labels[int(0.85 * len(labels)):]
        boxes = boxes[int(0.85 * len(boxes)):]
        landmarks = landmarks[int(0.85 * len(landmarks)):]
    ima = tf.data.Dataset.from_tensor_slices(images)
    lab = tf.data.Dataset.from_tensor_slices(labels)
    roi = tf.data.Dataset.from_tensor_slices(boxes)
    land = tf.data.Dataset.from_tensor_slices(landmarks)
    # ima,lab,roi = preprocess(ima,lab,roi)
    train_data = tf.data.Dataset.zip((ima, lab, roi, land)).shuffle(1000).batch(8)
    train_data = list(train_data.as_numpy_iterator())
    return train_data

In [9]:
data = load_pokemon("train")

KeyboardInterrupt: 

In [5]:
print(len(data))

2079


In [4]:
def train(epoches):
    model = Pnet()
    if os.path.exists("pnet.h5"):
        model.load_weights("pnet.h5")
    else:
        model.load_weights('./Weights/pnet_wight/pnet_30.ckpt')
 
    optimizer = keras.optimizers.Adam(learning_rate=1e-3)
    off = 1000
    acc_meter = metrics.Accuracy()
    for epoch in tqdm(range(epoches)):
 
        for i,(img,lab,boxes,landmarks) in enumerate(load_pokemon("train")):
 
 
            #img = image_color_distort(img)
            # 开一个gradient tape, 计算梯度
            with tf.GradientTape() as tape:
                cls_prob, bbox_pred, landmark_pred = model(img)
                cls_prob = tf.squeeze(cls_prob,[1,2])
                bbox_pred = tf.squeeze(bbox_pred,[1,2])
                landmark_pred = tf.squeeze(landmark_pred,[1,2])
 
                cls_loss = cls_ohem(cls_prob, lab)
                bbox_loss = bbox_ohem(bbox_pred, boxes,lab)
                landmark_loss = landmark_ohem(landmark_pred, landmarks, lab)
                # accuracy = cal_accuracy(cls_prob, label_batch)
                
                print(cls_loss)
                print(bbox_loss)
                print(landmark_loss)
    
                total_loss_value = cls_loss + 0.5 * bbox_loss + 0.5 * landmark_loss
                grads = tape.gradient(total_loss_value, model.trainable_variables)
                optimizer.apply_gradients(zip(grads, model.trainable_variables))
            if i % 200 == 0:
                print('Training loss (for one batch) at step %s: %s' % (i, float(total_loss_value)))
                print('Seen so far: %s samples' % ((i + 1) * 8))
 
 
        for i, (v_img, v_lab1, boxes,landmarks) in enumerate(load_pokemon("val")):
            v_img = image_color_distort(v_img)
            with tf.GradientTape() as tape:
                cls_prob, bbox_pred, landmark_pred = model(v_img)
                cls_prob = tf.squeeze(cls_prob,[1,2])
                bbox_pred = tf.squeeze(bbox_pred,[1,2])
                landmark_pred = tf.squeeze(landmark_pred,[1,2])
 
                cls_loss = cls_ohem(cls_prob, v_lab1)
                bbox_loss = bbox_ohem(bbox_pred, boxes,v_lab1)
                landmark_loss = landmark_ohem(landmark_pred, landmarks, v_lab1)
                # accuracy = cal_accuracy(cls_prob, label_batch)
 
 
                total_loss_value = cls_loss + 0.5 * bbox_loss + 0.5 * landmark_loss
                grads = tape.gradient(total_loss_value, model.trainable_variables)
                optimizer.apply_gradients(zip(grads, model.trainable_variables))
            if i % 200 == 0:
                print('val___ loss (for one batch) at step %s: %s' % (i, float(total_loss_value)))
                print('Seen so far: %s samples' % ((i + 1) * 8))
    model.save_weights('./Weights/pnet_wight/pnet_30.ckpt')

In [5]:
train(10)

  0%|          | 0/10 [00:00<?, ?it/s]

tf.Tensor(0.0381509, shape=(), dtype=float32)
tf.Tensor(0.044728015, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
Training loss (for one batch) at step 0: 0.0605149045586586
Seen so far: 8 samples
tf.Tensor(0.028697459, shape=(), dtype=float32)
tf.Tensor(0.0533701, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.17707749, shape=(), dtype=float32)
tf.Tensor(0.043022223, shape=(), dtype=float32)
tf.Tensor(15.363095, shape=(), dtype=float32)
tf.Tensor(0.0070076603, shape=(), dtype=float32)
tf.Tensor(0.06267925, shape=(), dtype=float32)
tf.Tensor(20.51806, shape=(), dtype=float32)
tf.Tensor(0.00014337614, shape=(), dtype=float32)
tf.Tensor(0.06530244, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.06291271, shape=(), dtype=float32)
tf.Tensor(0.07196217, shape=(), dtype=float32)
tf.Tensor(16.372868, shape=(), dtype=float32)
tf.Tensor(0.0005358209, shape=(), dtype=float32)
tf.Tensor(0.014668062, shape=(), dtype=fl

tf.Tensor(0.274084, shape=(), dtype=float32)
tf.Tensor(0.058287896, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.033491343, shape=(), dtype=float32)
tf.Tensor(0.037683766, shape=(), dtype=float32)
tf.Tensor(3.2857242, shape=(), dtype=float32)
tf.Tensor(0.24650343, shape=(), dtype=float32)
tf.Tensor(0.05824227, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.0120608155, shape=(), dtype=float32)
tf.Tensor(0.034664385, shape=(), dtype=float32)
tf.Tensor(9.76988, shape=(), dtype=float32)
tf.Tensor(0.029797336, shape=(), dtype=float32)
tf.Tensor(0.024735786, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.5573604, shape=(), dtype=float32)
tf.Tensor(0.10565151, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.09498154, shape=(), dtype=float32)
tf.Tensor(0.019533433, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.01828844, shape=(), dtype=float32)

tf.Tensor(0.125509, shape=(), dtype=float32)
tf.Tensor(0.12579846, shape=(), dtype=float32)
tf.Tensor(0.45823026, shape=(), dtype=float32)
tf.Tensor(0.1565875, shape=(), dtype=float32)
tf.Tensor(0.07074608, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.25292116, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.023048755, shape=(), dtype=float32)
tf.Tensor(0.08998913, shape=(), dtype=float32)
tf.Tensor(3.369761, shape=(), dtype=float32)
tf.Tensor(0.12281552, shape=(), dtype=float32)
tf.Tensor(0.06352657, shape=(), dtype=float32)
tf.Tensor(3.6918786, shape=(), dtype=float32)
tf.Tensor(0.3164513, shape=(), dtype=float32)
tf.Tensor(0.068633795, shape=(), dtype=float32)
tf.Tensor(1.3927621, shape=(), dtype=float32)
tf.Tensor(0.29819015, shape=(), dtype=float32)
tf.Tensor(0.13368054, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.11989995, shape=(), dtype=float32)


tf.Tensor(0.6256585, shape=(), dtype=float32)
tf.Tensor(0.099605516, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.22337131, shape=(), dtype=float32)
tf.Tensor(0.11873533, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.11359243, shape=(), dtype=float32)
tf.Tensor(0.081074335, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.7851396, shape=(), dtype=float32)
tf.Tensor(0.14228581, shape=(), dtype=float32)
tf.Tensor(1.4681197, shape=(), dtype=float32)
tf.Tensor(1.0905253, shape=(), dtype=float32)
tf.Tensor(0.033447135, shape=(), dtype=float32)
tf.Tensor(3.2463965, shape=(), dtype=float32)
tf.Tensor(0.8669367, shape=(), dtype=float32)
tf.Tensor(0.07725695, shape=(), dtype=float32)
tf.Tensor(1.9330955, shape=(), dtype=float32)
tf.Tensor(0.028171703, shape=(), dtype=float32)
tf.Tensor(0.08361338, shape=(), dtype=float32)
tf.Tensor(1.2181089, shape=(), dtype=float32)
tf.Tensor(0.02001788, shape=(), dtype=

...

tf.Tensor(0.0018709686, shape=(), dtype=float32)
tf.Tensor(0.08245406, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.0037374126, shape=(), dtype=float32)
tf.Tensor(0.12763649, shape=(), dtype=float32)
tf.Tensor(0.09073143, shape=(), dtype=float32)
tf.Tensor(0.0054099495, shape=(), dtype=float32)
tf.Tensor(0.050297715, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.5745951, shape=(), dtype=float32)
tf.Tensor(0.033512823, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.011770395, shape=(), dtype=float32)
tf.Tensor(0.033816796, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.03197324, shape=(), dtype=float32)
tf.Tensor(0.051954433, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.05047973, shape=(), dtype=float32)
tf.Tensor(0.084374286, shape=(), dtype=float32)
tf.Tensor(0.0843366, shape=(), dtype=float32)
tf.Tensor(0.0030283933, shape=(), dtyp

tf.Tensor(0.0108813485, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.1154548, shape=(), dtype=float32)
tf.Tensor(0.007897971, shape=(), dtype=float32)
tf.Tensor(0.050279498, shape=(), dtype=float32)
tf.Tensor(0.022271378, shape=(), dtype=float32)
tf.Tensor(0.020075195, shape=(), dtype=float32)
tf.Tensor(0.15724318, shape=(), dtype=float32)
tf.Tensor(0.024402007, shape=(), dtype=float32)
tf.Tensor(0.022229277, shape=(), dtype=float32)
tf.Tensor(0.037613288, shape=(), dtype=float32)
tf.Tensor(0.056680247, shape=(), dtype=float32)
tf.Tensor(0.026945082, shape=(), dtype=float32)
tf.Tensor(0.024995208, shape=(), dtype=float32)
tf.Tensor(0.04280712, shape=(), dtype=float32)
tf.Tensor(0.023478122, shape=(), dtype=float32)
tf.Tensor(0.08760663, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.2968795, shape=(), dtype=float32)
tf.Tensor(0.0885319, shape=(), dtype=float32)
tf.Tensor(0.0, shape=(), dtype=float32)
tf.Tensor(0.67895734, sh

val___ loss (for one batch) at step 200: 0.1568268984556198
Seen so far: 1608 samples


val___ loss (for one batch) at step 400: 0.18877491354942322
Seen so far: 3208 samples


100%|██████████| 10/10 [15:53<00:00, 95.34s/it]
